In [1]:
import torch
import random
import numpy as np
import os

from tqdm import tqdm, trange
# torch.cuda.empty_cache()
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
from pytorch_pretrained_bert.optimization import BertAdam
# from pytorch_pretrained_bert.tokenization import BertTokenizer, WordpieceTokenizer

In [2]:
from run_classifier import ColaProcessor, MrpcProcessor, logger, convert_examples_to_features,\
    set_optimizer_params_grad, copy_optimizer_params_to_model, accuracy, p_r_f1, tp_pcount_gcount, convert_claims_to_features

In [3]:
if torch.cuda.is_available():    

    # Tell PyTorch to use the GPU.    
    device = torch.device("cuda")
    n_gpu = torch.cuda.device_count()
#     device = torch.device("cpu")
    print('There are %d GPU(s) available.' % n_gpu)

    print('We will use the GPU:', torch.cuda.get_device_name(0))

# If not...
else:
    print('No GPU available, using the CPU instead.')
    device = torch.device("cpu")

There are 1 GPU(s) available.
We will use the GPU: GeForce GTX 1050 Ti


In [4]:
from transformers import BertTokenizer, AdamW, get_linear_schedule_with_warmup
from pytorch_pretrained_bert.modeling import BertForSequenceClassification, BertPreTrainedModel, BertModel, BertConfig
from torch.nn import BCEWithLogitsLoss, CosineEmbeddingLoss,CrossEntropyLoss, MSELoss

06/23/2020 18:56:43 - INFO - transformers.file_utils -   PyTorch version 1.4.0 available.
06/23/2020 18:57:32 - INFO - transformers.file_utils -   TensorFlow version 2.1.0 available.


In [5]:
# import logging
# logging.basicConfig(level=logging.INFO)

In [6]:
# def train_and_test(data_dir, bert_model="bert-base-uncased", task_name=None,
#                    output_dir=None, max_seq_length=128, do_train=False, do_eval=False, do_lower_case=False,
#                    train_batch_size=32, eval_batch_size=8, learning_rate=5e-5, num_train_epochs=3,
#                    warmup_proportion=0.1,no_cuda=False, local_rank=-1, seed=42, gradient_accumulation_steps=1,
#                    optimize_on_cpu=False, fp16=False, loss_scale=128, saved_model=""):

In [11]:
class BertForConsistencyCueClassification(BertPreTrainedModel):
    def __init__(self, config, num_labels=2):
        super(BertForConsistencyCueClassification, self).__init__(config)
        self.num_labels = num_labels

        self.bert = BertModel(config)
        self.dropout = torch.nn.Dropout(config.hidden_dropout_prob)
        self.classifier = torch.nn.Linear(config.hidden_size+1, num_labels)
        self.classifier2 = torch.nn.Linear(config.hidden_size, num_labels)
        self.apply(self.init_bert_weights)
#         self.init_weights()

#     @add_start_docstrings_to_callable(BERT_INPUTS_DOCSTRING)
    def forward(
        self,
        input_ids=None,
        attention_mask=None,
        token_type_ids=None,
        position_ids=None,
        head_mask=None,
        inputs_embeds=None,
        labels=None,
        input_ids2=None,
        attention_mask2=None,
        token_type_ids2=None,
        position_ids2=None,
        head_mask2=None,
        inputs_embeds2=None,
        labels2=None,
    ):
        r"""
        labels (:obj:`torch.LongTensor` of shape :obj:`(batch_size,)`, `optional`, defaults to :obj:`None`):
            Labels for computing the sequence classification/regression loss.
            Indices should be in :obj:`[0, ..., config.num_labels - 1]`.
            If :obj:`config.num_labels == 1` a regression loss is computed (Mean-Square loss),
            If :obj:`config.num_labels > 1` a classification loss is computed (Cross-Entropy).

    Returns:
        :obj:`tuple(torch.FloatTensor)` comprising various elements depending on the configuration (:class:`~transformers.BertConfig`) and inputs:
        loss (:obj:`torch.FloatTensor` of shape :obj:`(1,)`, `optional`, returned when :obj:`label` is provided):
            Classification (or regression if config.num_labels==1) loss.
        logits (:obj:`torch.FloatTensor` of shape :obj:`(batch_size, config.num_labels)`):
            Classification (or regression if config.num_labels==1) scores (before SoftMax).
        hidden_states (:obj:`tuple(torch.FloatTensor)`, `optional`, returned when ``config.output_hidden_states=True``):
            Tuple of :obj:`torch.FloatTensor` (one for the output of the embeddings + one for the output of each layer)
            of shape :obj:`(batch_size, sequence_length, hidden_size)`.

            Hidden-states of the model at the output of each layer plus the initial embedding outputs.
        attentions (:obj:`tuple(torch.FloatTensor)`, `optional`, returned when ``config.output_attentions=True``):
            Tuple of :obj:`torch.FloatTensor` (one for each layer) of shape
            :obj:`(batch_size, num_heads, sequence_length, sequence_length)`.

            Attentions weights after the attention softmax, used to compute the weighted average in the self-attention
            heads.

    Examples::

        from transformers import BertTokenizer, BertForSequenceClassification
        import torch

        tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
        model = BertForSequenceClassification.from_pretrained('bert-base-uncased')

        input_ids = torch.tensor(tokenizer.encode("Hello, my dog is cute", add_special_tokens=True)).unsqueeze(0)  # Batch size 1
        labels = torch.tensor([1]).unsqueeze(0)  # Batch size 1
        outputs = model(input_ids, labels=labels)

        loss, logits = outputs[:2]

        """

        _, outputs = self.bert(
            input_ids,
            attention_mask=attention_mask,
            token_type_ids=token_type_ids,
#             position_ids=position_ids,
#             head_mask=head_mask,
#             inputs_embeds=inputs_embeds,
        )

        _, outputsC = self.bert(
            input_ids2,
            attention_mask=attention_mask2,
            token_type_ids=token_type_ids2,
#             position_ids=position_ids2,
#             head_mask=head_mask2,
#             inputs_embeds=inputs_embeds2,
        )
#         print("Careful, outputs:")
#         print(outputs)
#         print(outputsC)
        pooled_output = outputs
        pooled_outputC = outputsC

        pooled_output = self.dropout(pooled_output)
        pooled_outputC = self.dropout(pooled_outputC)
        
        cos_pooled_outputs = torch.cosine_similarity(pooled_output, pooled_outputC, dim=1)
        
#         print('pooled_output size:')
#         print(pooled_output.size())
#         print(pooled_output)
#         print('cos_pooled_outputs size:')
#         print(cos_pooled_outputs.size())
#         print(cos_pooled_outputs)
        batch_size = list(pooled_output.size())[0]
        hidden_size = list(pooled_output.size())[1]

        logits_ce = self.classifier2(pooled_output)
        print('logits_ce:')
        print(logits_ce)
        
    
        ## v2: concat
        ## v3: multiply
        ## v4: v2 & ce_cos_similarity
        ## v5: v3 & ce_cos_similarity
        
#         print(torch.cat((pooled_output, cos_pooled_outputs.unsqueeze(1)),1))
#         print((pooled_output*cos_pooled_outputs.unsqueeze(1)))
        logits_cos = self.classifier(torch.cat((pooled_output, cos_pooled_outputs.unsqueeze(1)),1))
#         logits_cos = self.classifier2((pooled_output*cos_pooled_outputs.unsqueeze(1)))
#         self.classifier = torch.nn.Linear(hidden_size+batch_size, 2).to(device)
#         logits_cos = self.classifier(torch.cat((pooled_output, cos_pooled_outputs.repeat(batch_size,1)),1))
        print('logits_cos:')
        print(logits_cos)
        
#         logits = self.classifier(pooled_output)
#         logitsC = self.classifier(pooled_outputC)

#         outputs = (logits,) + outputs[2:]  # add hidden states and attention if they are here
#         print(logits)
#         print('xd')
#         print(outputs[2:])
#         outputs = (logits,) + outputs[2:]
#         print("labels:")
#         print(labels)
        if labels is not None:
            if self.num_labels == 1:
                #  We are doing regression
                loss_fct = MSELoss()
                loss = loss_fct(logits.view(-1), labels.view(-1))
            else:
#                 loss_fct_ce = CrossEntropyLoss()
#                 loss_ce = loss_fct(logits.view(-1, self.num_labels), labels.view(-1))

                loss_fct_ce = CrossEntropyLoss()
#                 print('pooled_output size:')
#                 print(pooled_output.size())
                loss_ce = loss_fct_ce(logits_ce.view(-1, self.num_labels), labels.view(-1))
#                 loss_ce = loss_fct_ce(pooled_output.view(-1), labels.view(-1))
#                 print('loss_ce:')
#                 print(loss_ce)

                
                loss_fct_cos = CosineEmbeddingLoss()
#                 print(labels)
#                 print(pooled_outputC)


#                 labels2[labels2==0] = -1
#                 loss_cos = loss_fct_cos(pooled_output, pooled_outputC, labels2)
        
        
#                 loss_cos = loss_fct_cos(logits_ce, logits_cos, labels2)
                loss_cos = loss_fct_ce(logits_cos.view(-1, self.num_labels), labels2.view(-1))
#                 print('loss_cos:')
#                 print(loss_cos)
            
                loss = loss_ce + loss_cos
#                 print('final loss:')
#                 print(loss)
#                 logits = self.classifier(loss)
#             outputs = (loss,) + outputs
#             outputs = (loss,) + logits_cos 
                outputs = loss
                return outputs
        else:
            return logits_cos
        
          # (loss), logits, (hidden_states), (attentions)


In [8]:
# labe = torch.ones(8)
# print(labe )
# labe[labe==1] = -1
# labe

In [9]:
# a = torch.tensor([[4.2,5,6,7,8],[9,10,11,12,13]])
# b = torch.tensor([[3.4,5,6,7,8],[9,10,11,12,13]])

# # a = torch.tensor([[4,5,6,7,8],[9,10,11,12,13]])
# # b = torch.tensor([1,2])
# c= torch.cosine_similarity(a,b,dim=1)
# # b.unsqueeze(1)
# # # a.size()
# # torch.cat((a,c.unsqueeze(1)),1)
# a*c.unsqueeze(1)

In [10]:
# input1 = torch.randn(100, 128)
# input2 = torch.randn(100, 128)
# output = torch.cosine_similarity(input1, input2, dim=1)

In [11]:
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

05/22/2020 12:38:49 - INFO - transformers.tokenization_utils -   loading file https://s3.amazonaws.com/models.huggingface.co/bert/bert-base-uncased-vocab.txt from cache at C:\Users\arsen\.cache\torch\transformers\26bc1ad6c0ac742e9b52263248f6d0f00068293b33709fae12320c0e35ccfbbb.542ce4285a40d23a559526243235df47c5f75c197f04f37d1a0c124c32c9a084


In [12]:
# Prepare model 
model = BertForConsistencyCueClassification.from_pretrained('bert-base-uncased', num_labels=2)
model.to(device)

# model = BertModel.from_pretrained('bert-base-uncased')

05/22/2020 12:38:50 - INFO - pytorch_pretrained_bert.modeling -   loading archive file https://s3.amazonaws.com/models.huggingface.co/bert/bert-base-uncased.tar.gz from cache at C:\Users\arsen\.pytorch_pretrained_bert\9c41111e2de84547a463fd39217199738d1e3deb72d4fec4399e6e241983c6f0.ae3cef932725ca7a30cdcb93fc6e09150a55e2a130ec7af63975a16c153ae2ba
05/22/2020 12:38:50 - INFO - pytorch_pretrained_bert.modeling -   extracting archive file C:\Users\arsen\.pytorch_pretrained_bert\9c41111e2de84547a463fd39217199738d1e3deb72d4fec4399e6e241983c6f0.ae3cef932725ca7a30cdcb93fc6e09150a55e2a130ec7af63975a16c153ae2ba to temp dir C:\Users\arsen\AppData\Local\Temp\tmpfur45zzk
05/22/2020 12:38:54 - INFO - pytorch_pretrained_bert.modeling -   Model config {
  "attention_probs_dropout_prob": 0.1,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "max_position_embeddings": 512,
  "num_attention_heads": 12,
  "num_hidden_lay

BertForConsistencyCueClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): BertLayerNorm()
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): BertLayerNorm()
              (dropout): Dropout(p=0.1, inplace=Fals

In [13]:
# Get all of the model's parameters as a list of tuples.
params = list(model.named_parameters())

print('The BERT model has {:} different named parameters.\n'.format(len(params)))

print('==== Embedding Layer ====\n')

for p in params[0:5]:
    print("{:<55} {:>12}".format(p[0], str(tuple(p[1].size()))))

print('\n==== First Transformer ====\n')

for p in params[5:21]:
    print("{:<55} {:>12}".format(p[0], str(tuple(p[1].size()))))
    
print('\n==== Output Layer ====\n')

for p in params[-4:]:
    print("{:<55} {:>12}".format(p[0], str(tuple(p[1].size()))))

The BERT model has 203 different named parameters.

==== Embedding Layer ====

bert.embeddings.word_embeddings.weight                  (30522, 768)
bert.embeddings.position_embeddings.weight                (512, 768)
bert.embeddings.token_type_embeddings.weight                (2, 768)
bert.embeddings.LayerNorm.weight                              (768,)
bert.embeddings.LayerNorm.bias                                (768,)

==== First Transformer ====

bert.encoder.layer.0.attention.self.query.weight          (768, 768)
bert.encoder.layer.0.attention.self.query.bias                (768,)
bert.encoder.layer.0.attention.self.key.weight            (768, 768)
bert.encoder.layer.0.attention.self.key.bias                  (768,)
bert.encoder.layer.0.attention.self.value.weight          (768, 768)
bert.encoder.layer.0.attention.self.value.bias                (768,)
bert.encoder.layer.0.attention.output.dense.weight        (768, 768)
bert.encoder.layer.0.attention.output.dense.bias              (

In [14]:
# data_dir = "D:/Jupyter/data/dataset/perspective_stances/"
data_dir = "D:/Projects/Stance/Dataset/BertForOppositeClassification/"
# data_dir_output = "D:/Projects/Stance/Models/Consistency_Cues/"
data_dir_output = "D:/Projects/Stance/Models/dataExpantion/"
output_dir=data_dir_output
max_seq_length=32
max_grad_norm = 1.0
num_training_steps = 1000
num_warmup_steps = 100
warmup_proportion = float(num_warmup_steps) / float(num_training_steps)  # 0.1
# warmup_proportion = 0.1
train_batch_size=16
eval_batch_size=8
learning_rate=5e-5
num_train_epochs=3
local_rank=-1
seed=42
gradient_accumulation_steps=1
loss_scale=128
train_batch_size = int(train_batch_size / gradient_accumulation_steps)

processors = {
        "mrpc": MrpcProcessor,
    }

random.seed(seed)
np.random.seed(seed)
torch.manual_seed(seed)
torch.cuda.manual_seed_all(seed)
    
os.makedirs(output_dir, exist_ok=True)
processor = processors['mrpc']()
label_list = processor.get_labels()
num_labels = len(label_list)
# print('label list')
# print(label_list)

train_examples = processor.get_train_examples(data_dir)
num_train_steps = int(
    len(train_examples) / train_batch_size / gradient_accumulation_steps * num_train_epochs)

##preprare optimizer
param_optimizer = list(model.named_parameters())
no_decay = ['bias', 'gamma', 'beta']
optimizer_grouped_parameters = [
    {'params': [p for n, p in param_optimizer if not any(nd in n for nd in no_decay)], 'weight_decay_rate': 0.01},
    {'params': [p for n, p in param_optimizer if any(nd in n for nd in no_decay)], 'weight_decay_rate': 0.0}
    ]
t_total = num_train_steps
optimizer = BertAdam(optimizer_grouped_parameters,
                         lr=learning_rate,
                         warmup=warmup_proportion,
                         t_total=t_total)
# optimizer = AdamW(optimizer_grouped_parameters,
#                   lr = learning_rate, # args.learning_rate - default is 5e-5, our notebook had 2e-5
#                   eps = 1e-8, # args.adam_epsilon  - default is 1e-8.
#                   correct_bias=False
#                 )

# scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=num_warmup_steps, num_training_steps=t_total)  # PyTorch scheduler

05/22/2020 12:38:57 - INFO - run_classifier -   LOOKING AT D:/Projects/Stance/Dataset/BertForOppositeClassification/train.tsv


In [15]:
global_step = 0
train_features = convert_examples_to_features(train_examples, label_list, max_seq_length, tokenizer)
claim_features = convert_claims_to_features(train_examples, label_list, max_seq_length, tokenizer)
logger.info("***** Running training *****")
logger.info("  Num examples = %d", len(train_examples))
logger.info("  Batch size = %d", train_batch_size)
logger.info("  Num steps = %d", num_train_steps)


all_input_ids = torch.tensor([f.input_ids for f in train_features], dtype=torch.long)
all_input_mask = torch.tensor([f.input_mask for f in train_features], dtype=torch.long)
all_segment_ids = torch.tensor([f.segment_ids for f in train_features], dtype=torch.long)
all_label_ids = torch.tensor([f.label_id for f in train_features], dtype=torch.long)

claims_input_ids = torch.tensor([f.input_ids for f in claim_features], dtype=torch.long)
claims_input_mask = torch.tensor([f.input_mask for f in claim_features], dtype=torch.long)
claims_segment_ids = torch.tensor([f.segment_ids for f in claim_features], dtype=torch.long)
claims_label_ids = torch.tensor([f.label_id for f in claim_features], dtype=torch.long)

train_data = TensorDataset(all_input_ids, all_input_mask, all_segment_ids, all_label_ids, claims_input_ids, claims_input_mask, claims_segment_ids, claims_label_ids)
train_sampler = RandomSampler(train_data)
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=train_batch_size)

# claims_data = TensorDataset(claims_input_ids, claims_input_mask, claims_segment_ids, claims_label_ids)
# claims_sampler = RandomSampler(claims_data)
# claims_dataloader = DataLoader(claims_data, sampler=train_sampler, batch_size=train_batch_size)

05/22/2020 12:38:57 - INFO - run_classifier -   *** Example ***
05/22/2020 12:38:57 - INFO - run_classifier -   guid: train-1
05/22/2020 12:38:57 - INFO - run_classifier -   tokens: [CLS] male infant ci ##rc ##um ##cision is tan ##tam ##ount to child abuse [SEP] parents have the right to use their best judgment , in the light of medical advice [SEP]
05/22/2020 12:38:57 - INFO - run_classifier -   input_ids: 101 3287 10527 25022 11890 2819 28472 2003 9092 15464 21723 2000 2775 6905 102 3008 2031 1996 2157 2000 2224 2037 2190 8689 1010 1999 1996 2422 1997 2966 6040 102
05/22/2020 12:38:57 - INFO - run_classifier -   input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
05/22/2020 12:38:57 - INFO - run_classifier -   segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
05/22/2020 12:38:57 - INFO - run_classifier -   label: 0 (id = 0)
05/22/2020 12:38:57 - INFO - run_classifier -   *** Example ***
05/22/2020 12:38:57 - INFO - run_classifier -  

In [16]:
model.train()
for _ in trange(int(num_train_epochs), desc="Epoch"):
    tr_loss = 0
    nb_tr_examples, nb_tr_steps = 0, 0
    for step, batch in enumerate(tqdm(train_dataloader, desc="Iteration")):
        batch = tuple(t.to(device) for t in batch)
        input_ids, input_mask, segment_ids, label_ids, claim_input_ids, claim_input_mask, claim_segment_ids, claim_label_ids = batch
#         ce_loss = model(input_ids, segment_ids, input_mask, label_ids)
#         cos_loss = model(claim_input_ids, claim_segment_ids, claim_input_mask, claim_label_ids)
        
#         print("start")
#         print(input_ids)
#         print(input_mask)
#         print(segment_ids)
#         print(label_ids)
#         print(claim_input_ids)
#         print(claim_input_mask)
#         print(claim_segment_ids)
#         print(claim_label_ids)
#         print("end")
    
        out_results = model(input_ids=input_ids, token_type_ids=segment_ids, attention_mask=input_mask, labels=label_ids, input_ids2=claim_input_ids, token_type_ids2=claim_segment_ids, attention_mask2=claim_input_mask, labels2=claim_label_ids)
#         loss = ce_loss + cos_loss
        print("out_results:")
        print(out_results)
        loss = out_results
#         print(cos_loss)
#         print(loss.item())
        if n_gpu > 1:
            loss = loss.mean() # mean() to average on multi-gpu.
#         if fp16 and loss_scale != 1.0:
#             # rescale loss for fp16 training
#             # see https://docs.nvidia.com/deeplearning/sdk/mixed-precision-training/index.html
#             loss = loss * loss_scale
        if gradient_accumulation_steps > 1:
            loss = loss / gradient_accumulation_steps
        loss.backward()
        
        tr_loss += loss.item()
        nb_tr_examples += input_ids.size(0)
        nb_tr_steps += 1
        if (step + 1) % gradient_accumulation_steps == 0:
#             if fp16 or optimize_on_cpu:
#                 if fp16 and loss_scale != 1.0:
#                     # scale down gradients for fp16 training
#                     for param in model.parameters():
#                         if param.grad is not None:
#                             param.grad.data = param.grad.data / loss_scale           
#                 is_nan = set_optimizer_params_grad(param_optimizer, model.named_parameters(), test_nan=True)
#                 if is_nan:
#                     logger.info("FP16 TRAINING: Nan in gradients, reducing loss scaling")
#                     loss_scale = loss_scale / 2
#                     model.zero_grad()
#                     continue 
#                 optimizer.step()
# #                 scheduler.step()
#                 copy_optimizer_params_to_model(model.named_parameters(), param_optimizer)
#             else:
#                 torch.nn.utils.clip_grad_norm_(model.parameters(), max_grad_norm)
            optimizer.step()
#                 scheduler.step()
            model.zero_grad()
            global_step += 1

        
## v2: concat
## v3: multiply
model_to_save = model.module if hasattr(model, 'module') else model
torch.save(model.state_dict(), output_dir + "consistencycue_expansion.pth")
torch.save(model_to_save.state_dict(), output_dir + "finetuned_consistencycues_expansion.bin")

Iteration:   0%|                                                                               | 0/830 [00:00<?, ?it/s]

logits_ce:
tensor([[ 0.1799,  1.0070],
        [ 0.0385,  0.6859],
        [ 0.1871,  0.7877],
        [ 0.2292,  0.7926],
        [-0.0580,  0.8326],
        [ 0.1220,  0.5854],
        [-0.0887,  0.6823],
        [ 0.2489,  0.5384],
        [ 0.0143,  0.8160],
        [ 0.4310,  0.8450],
        [ 0.0295,  0.8351],
        [ 0.1543,  1.0602],
        [ 0.0900,  1.0443],
        [ 0.3337,  0.5424],
        [-0.1713,  1.0689],
        [ 0.1686,  0.7449]], device='cuda:0', grad_fn=<AddmmBackward>)
logits_cos:
tensor([[-1.4780, -0.2056],
        [-1.3604, -0.1818],
        [-1.2883, -0.0999],
        [-1.4083, -0.2302],
        [-1.4670,  0.1158],
        [-1.5024, -0.2097],
        [-1.5235, -0.2283],
        [-1.5648, -0.4125],
        [-1.5900, -0.4696],
        [-1.2437, -0.0766],
        [-1.5481, -0.4316],
        [-1.3451, -0.1847],
        [-1.1656, -0.1183],
        [-0.8416, -0.1753],
        [-1.3973, -0.0676],
        [-1.3559, -0.0999]], device='cuda:0', grad_fn=<AddmmBackwa


Iteration:   0%|                                                                       | 1/830 [00:01<14:21,  1.04s/it]

logits_ce:
tensor([[ 0.0054,  1.1790],
        [ 0.1025,  0.7234],
        [ 0.0097,  1.1857],
        [ 0.2172,  0.8839],
        [ 0.2009,  0.8954],
        [ 0.0965,  1.3139],
        [ 0.1390,  0.7632],
        [ 0.1204,  0.6783],
        [ 0.4109,  1.0192],
        [-0.0584,  1.0511],
        [-0.0943,  1.1136],
        [ 0.3323,  0.8109],
        [ 0.3682,  0.8580],
        [ 0.1945,  0.8310],
        [ 0.2982,  0.4610],
        [ 0.2453,  0.9733]], device='cuda:0', grad_fn=<AddmmBackward>)
logits_cos:
tensor([[-1.2278, -0.3915],
        [-1.2739, -0.2991],
        [-1.3404,  0.0726],
        [-0.8705, -0.1792],
        [-1.4332, -0.3242],
        [-1.2025, -0.2411],
        [-1.4344, -0.2682],
        [-1.1713, -0.0144],
        [-1.5065, -0.1693],
        [-1.5309, -0.3251],
        [-1.4907, -0.0470],
        [-0.9452, -0.0075],
        [-1.5238, -0.3269],
        [-1.0078, -0.0848],
        [-0.5829, -0.1353],
        [-1.3422,  0.0041]], device='cuda:0', grad_fn=<AddmmBackwa


Iteration:   0%|▏                                                                      | 2/830 [00:01<13:07,  1.05it/s]

...


Iteration: 100%|██████████████████████████████████████████████████████████████████▊| 828/830 [1:12:11<00:03,  1.85s/it]

logits_ce:
tensor([[ 0.0940,  0.0723],
        [-2.6001,  2.8635],
        [ 0.7867, -1.6751],
        [-2.0381,  2.5747],
        [ 0.8942, -1.5567],
        [ 2.0197, -2.6335],
        [ 2.3965, -3.1597],
        [-1.6777,  1.9109],
        [-2.2182,  2.4615],
        [-2.6116,  3.0823],
        [ 1.8611, -2.2489],
        [-2.9767,  3.1082],
        [ 2.0642, -2.6719],
        [ 1.6484, -2.3320],
        [-2.3352,  2.7610],
        [-1.5545,  1.6662]], device='cuda:0', grad_fn=<AddmmBackward>)
logits_cos:
tensor([[-0.0391, -0.0249],
        [-3.1336,  1.9620],
        [ 1.5422, -1.2876],
        [-2.5956,  1.7288],
        [ 1.3408, -1.0471],
        [ 2.9301, -1.7980],
        [ 3.3135, -1.9871],
        [-1.9792,  1.1037],
        [-2.7711,  1.8151],
        [-3.4274,  2.1244],
        [ 2.6715, -1.5037],
        [-3.7654,  2.2576],
        [ 2.8905, -1.8254],
        [ 2.5880, -1.7526],
        [-3.2782,  1.9521],
        [-2.1316,  0.9986]], device='cuda:0', grad_fn=<AddmmBackwa


Iteration: 100%|██████████████████████████████████████████████████████████████████▉| 829/830 [1:12:13<00:01,  1.85s/it]

logits_ce:
tensor([[-1.8190,  2.0660],
        [ 1.5190, -2.2098],
        [-2.4830,  2.8459],
        [ 1.6289, -2.1924],
        [ 1.0351, -1.4730],
        [ 2.2963, -2.7420],
        [-2.0415,  2.4406],
        [ 2.5924, -2.9236],
        [-1.8493,  2.6023],
        [ 1.4865, -2.2028],
        [-2.2231,  2.7277],
        [-2.1976,  2.5285],
        [ 2.7222, -3.2696]], device='cuda:0', grad_fn=<AddmmBackward>)
logits_cos:
tensor([[-2.5806,  1.2246],
        [ 2.1379, -1.4090],
        [-3.4322,  2.2153],
        [ 2.3548, -1.6951],
        [ 1.4678, -1.0954],
        [ 2.8799, -1.8359],
        [-2.8758,  1.6853],
        [ 3.3639, -2.3051],
        [-2.7229,  1.8135],
        [ 2.0246, -1.4809],
        [-2.9977,  1.6931],
        [-3.2357,  2.1776],
        [ 4.1145, -2.4583]], device='cuda:0', grad_fn=<AddmmBackward>)
out_results:
tensor(0.0345, device='cuda:0', grad_fn=<AddBackward0>)



Epoch: 100%|█████████████████████████████████████████████████████████████████████████| 3/3 [2:19:49<00:00, 2796.58s/it]


In [13]:
import csv
from pytorch_pretrained_bert.file_utils import PYTORCH_PRETRAINED_BERT_CACHE
def train_and_test(data_dir, bert_model="bert-base-uncased", task_name=None,
                   output_dir=None, max_seq_length=32, do_train=False, do_eval=False, do_lower_case=False,
                   train_batch_size=32, eval_batch_size=8, learning_rate=5e-5, num_train_epochs=3,
                   warmup_proportion=0.1,no_cuda=False, local_rank=-1, seed=19, gradient_accumulation_steps=1,
                   optimize_on_cpu=False, fp16=False, loss_scale=128, saved_model=""):


    # ## Required parameters
    # parser.add_argument("--data_dir",
    #                     default=None,
    #                     type=str,
    #                     required=True,
    #                     help="The input data dir. Should contain the .tsv files (or other data files) for the task.")
    # parser.add_argument("--bert_model", default=None, type=str, required=True,
    #                     help="Bert pre-trained model selected in the list: bert-base-uncased, "
    #                          "bert-large-uncased, bert-base-cased, bert-base-multilingual, bert-base-chinese.")
    # parser.add_argument("--task_name",
    #                     default=None,
    #                     type=str,
    #                     required=True,
    #                     help="The name of the task to train.")
    # parser.add_argument("--output_dir",
    #                     default=None,
    #                     type=str,
    #                     required=True,
    #                     help="The output directory where the model checkpoints will be written.")

    ## Other parameters
    # parser.add_argument("--max_seq_length",
    #                     default=128,
    #                     type=int,
    #                     help="The maximum total input sequence length after WordPiece tokenization. \n"
    #                          "Sequences longer than this will be truncated, and sequences shorter \n"
    #                          "than this will be padded.")
    # parser.add_argument("--do_train",
    #                     default=False,
    #                     action='store_true',
    #                     help="Whether to run training.")
    # parser.add_argument("--do_eval",
    #                     default=False,
    #                     action='store_true',
    #                     help="Whether to run eval on the dev set.")
    # parser.add_argument("--do_lower_case",
    #                     default=False,
    #                     action='store_true',
    #                     help="Set this flag if you are using an uncased model.")
    # parser.add_argument("--train_batch_size",
    #                     default=32,
    #                     type=int,
    #                     help="Total batch size for training.")
    # parser.add_argument("--eval_batch_size",
    #                     default=8,
    #                     type=int,
    #                     help="Total batch size for eval.")
    # parser.add_argument("--learning_rate",
    #                     default=5e-5,
    #                     type=float,
    #                     help="The initial learning rate for Adam.")
    # parser.add_argument("--num_train_epochs",
    #                     default=3.0,
    #                     type=float,
    #                     help="Total number of training epochs to perform.")
    # parser.add_argument("--warmup_proportion",
    #                     default=0.1,
    #                     type=float,
    #                     help="Proportion of training to perform linear learning rate warmup for. "
    #                          "E.g., 0.1 = 10%% of training.")
    # parser.add_argument("--no_cuda",
    #                     default=False,
    #                     action='store_true',
    #                     help="Whether not to use CUDA when available")
    # parser.add_argument("--local_rank",
    #                     type=int,
    #                     default=-1,
    #                     help="local_rank for distributed training on gpus")
    # parser.add_argument('--seed',
    #                     type=int,
    #                     default=42,
    #                     help="random seed for initialization")
    # parser.add_argument('--gradient_accumulation_steps',
    #                     type=int,
    #                     default=1,
    #                     help="Number of updates steps to accumulate before performing a backward/update pass.")
    # parser.add_argument('--optimize_on_cpu',
    #                     default=False,
    #                     action='store_true',
    #                     help="Whether to perform optimization and keep the optimizer averages on CPU")
    # parser.add_argument('--fp16',
    #                     default=False,
    #                     action='store_true',
    #                     help="Whether to use 16-bit float precision instead of 32-bit")
    # parser.add_argument('--loss_scale',
    #                     type=float, default=128,
    #                     help='Loss scaling, positive power of 2 values can improve fp16 convergence.')

    # args = parser.parse_args()

    processors = {
#         "cola": ColaProcessor,
#         "mnli": MnliProcessor,
        "mrpc": MrpcProcessor,
    }

    if local_rank == -1 or no_cuda:
        device = torch.device("cuda" if torch.cuda.is_available() and not no_cuda else "cpu")
        n_gpu = torch.cuda.device_count()
    else:
        device = torch.device("cuda", local_rank)
        n_gpu = 1
        # Initializes the distributed backend which will take care of sychronizing nodes/GPUs
        torch.distributed.init_process_group(backend='nccl')
        if fp16:
            logger.info("16-bits training currently not supported in distributed training")
            fp16 = False # (see https://github.com/pytorch/pytorch/pull/13496)
    logger.info("device %s n_gpu %d distributed training %r", device, n_gpu, bool(local_rank != -1))

    if gradient_accumulation_steps < 1:
        raise ValueError("Invalid gradient_accumulation_steps parameter: {}, should be >= 1".format(
                            gradient_accumulation_steps))

    train_batch_size = int(train_batch_size / gradient_accumulation_steps)

    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    if n_gpu > 0:
        torch.cuda.manual_seed_all(seed)

    if not do_train and not do_eval:
        raise ValueError("At least one of `do_train` or `do_eval` must be True.")

    if do_train:
        if os.path.exists(output_dir) and os.listdir(output_dir):
            raise ValueError("Output directory ({}) already exists and is not emp1ty.".format(output_dir))
        os.makedirs(output_dir, exist_ok=True)

    task_name = task_name.lower()

    if task_name not in processors:
        raise ValueError("Task not found: %s" % (task_name))

    processor = processors[task_name]()
    label_list = processor.get_labels()

#     tokenizer = BertTokenizer.from_pretrained(bert_model, do_lower_case=do_lower_case)
    tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

    train_examples = None
    num_train_steps = None
    if do_train:
        train_examples = processor.get_train_examples(data_dir)
        num_train_steps = int(
            len(train_examples) / train_batch_size / gradient_accumulation_steps * num_train_epochs)

    # Prepare model
#     model = BertForSequenceClassification.from_pretrained(bert_model,
#                 cache_dir=PYTORCH_PRETRAINED_BERT_CACHE / 'distributed_{}'.format(local_rank), num_labels = 2)

        model = BertForConsistencyCueClassification.from_pretrained('bert-base-uncased', num_labels=2)
        model.to(device)
        if fp16:
            model.half()

        if local_rank != -1:
            model = torch.nn.parallel.DistributedDataParallel(model, device_ids=[local_rank],
                                                              output_device=local_rank)
        elif n_gpu > 1:
            model = torch.nn.DataParallel(model)

        # Prepare optimizer
        if fp16:
            param_optimizer = [(n, param.clone().detach().to('cpu').float().requires_grad_()) \
                                for n, param in model.named_parameters()]
        elif optimize_on_cpu:
            param_optimizer = [(n, param.clone().detach().to('cpu').requires_grad_()) \
                                for n, param in model.named_parameters()]
        else:
            param_optimizer = list(model.named_parameters())
        no_decay = ['bias', 'gamma', 'beta']
        optimizer_grouped_parameters = [
            {'params': [p for n, p in param_optimizer if not any(nd in n for nd in no_decay)], 'weight_decay_rate': 0.01},
            {'params': [p for n, p in param_optimizer if any(nd in n for nd in no_decay)], 'weight_decay_rate': 0.0}
            ]
        t_total = num_train_steps
#     print(t_total)
    if local_rank != -1:
        t_total = t_total // torch.distributed.get_world_size()
    if do_train:
        optimizer = BertAdam(optimizer_grouped_parameters,
                         lr=learning_rate,
                         warmup=warmup_proportion,
                         t_total=t_total)

    global_step = 0
    if do_train:
        train_features = convert_examples_to_features(
            train_examples, label_list, max_seq_length, tokenizer)
        logger.info("***** Running training *****")
        logger.info("  Num examples = %d", len(train_examples))
        logger.info("  Batch size = %d", train_batch_size)
        logger.info("  Num steps = %d", num_train_steps)
        all_input_ids = torch.tensor([f.input_ids for f in train_features], dtype=torch.long)
        all_input_mask = torch.tensor([f.input_mask for f in train_features], dtype=torch.long)
        all_segment_ids = torch.tensor([f.segment_ids for f in train_features], dtype=torch.long)
        all_label_ids = torch.tensor([f.label_id for f in train_features], dtype=torch.long)
        train_data = TensorDataset(all_input_ids, all_input_mask, all_segment_ids, all_label_ids)
        if local_rank == -1:
            train_sampler = RandomSampler(train_data)
        else:
            train_sampler = DistributedSampler(train_data)
        train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=train_batch_size)

        model.train()
        for _ in trange(int(num_train_epochs), desc="Epoch"):
            tr_loss = 0
            nb_tr_examples, nb_tr_steps = 0, 0
            for step, batch in enumerate(tqdm(train_dataloader, desc="Iteration")):
                batch = tuple(t.to(device) for t in batch)
                input_ids, input_mask, segment_ids, label_ids, = batch
                loss = model(input_ids, segment_ids, input_mask, label_ids)
                if n_gpu > 1:
                    loss = loss.mean() # mean() to average on multi-gpu.
                if fp16 and loss_scale != 1.0:
                    # rescale loss for fp16 training
                    # see https://docs.nvidia.com/deeplearning/sdk/mixed-precision-training/index.html
                    loss = loss * loss_scale
                if gradient_accumulation_steps > 1:
                    loss = loss / gradient_accumulation_steps
                loss.backward()
                tr_loss += loss.item()
                nb_tr_examples += input_ids.size(0)
                nb_tr_steps += 1
                if (step + 1) % gradient_accumulation_steps == 0:
                    if fp16 or optimize_on_cpu:
                        if fp16 and loss_scale != 1.0:
                            # scale down gradients for fp16 training
                            for param in model.parameters():
                                if param.grad is not None:
                                    param.grad.data = param.grad.data / loss_scale
                        is_nan = set_optimizer_params_grad(param_optimizer, model.named_parameters(), test_nan=True)
                        if is_nan:
                            logger.info("FP16 TRAINING: Nan in gradients, reducing loss scaling")
                            loss_scale = loss_scale / 2
                            model.zero_grad()
                            continue
                        optimizer.step()
                        copy_optimizer_params_to_model(model.named_parameters(), param_optimizer)
                    else:
                        optimizer.step()
                    model.zero_grad()
                    global_step += 1

        torch.save(model.state_dict(), output_dir + "output.pth")


    if do_eval and (local_rank == -1 or torch.distributed.get_rank() == 0):
        eval_examples = processor.get_test_examples(data_dir)
#         eval_examples = processor.get_dev_examples(data_dir)
        eval_features = convert_examples_to_features(
            eval_examples, label_list, max_seq_length, tokenizer)
        claim_features = convert_claims_to_features(eval_examples, label_list, max_seq_length, tokenizer)    
    
        logger.info("***** Running evaluation *****")
        logger.info("  Num examples = %d", len(eval_examples))
        logger.info("  Batch size = %d", eval_batch_size)
        all_input_ids = torch.tensor([f.input_ids for f in eval_features], dtype=torch.long)
        all_input_mask = torch.tensor([f.input_mask for f in eval_features], dtype=torch.long)
        all_segment_ids = torch.tensor([f.segment_ids for f in eval_features], dtype=torch.long)
        all_label_ids = torch.tensor([f.label_id for f in eval_features], dtype=torch.long)
        
        claims_input_ids = torch.tensor([f.input_ids for f in claim_features], dtype=torch.long)
        claims_input_mask = torch.tensor([f.input_mask for f in claim_features], dtype=torch.long)
        claims_segment_ids = torch.tensor([f.segment_ids for f in claim_features], dtype=torch.long)
        claims_label_ids = torch.tensor([f.label_id for f in claim_features], dtype=torch.long)
        
        eval_data = TensorDataset(all_input_ids, all_input_mask, all_segment_ids, all_label_ids, claims_input_ids, claims_input_mask, claims_segment_ids, claims_label_ids)
        # Run prediction for full data
#         eval_sampler = SequentialSampler(eval_data)
        eval_sampler = SequentialSampler(eval_data)
        eval_dataloader = DataLoader(eval_data, sampler=eval_sampler, batch_size=eval_batch_size)
#         print('all_input_ids:')
#         print(all_input_ids)
        
        

#         model.load_state_dict(torch.load(saved_model))
        model_state_dict = torch.load(saved_model)
        model = BertForConsistencyCueClassification.from_pretrained('bert-base-uncased', num_labels=2, state_dict=model_state_dict)
        model.to(device)
        
        model.eval()
        # eval_loss, eval_accuracy = 0, 0

        eval_tp, eval_pred_c, eval_gold_c = 0, 0, 0
        eval_loss, eval_macro_p, eval_macro_r = 0, 0, 0

        raw_score = []

        nb_eval_steps, nb_eval_examples = 0, 0
        for input_ids, input_mask, segment_ids, label_ids, claim_input_ids, claim_input_mask, claim_segment_ids, claim_label_ids in eval_dataloader:
            input_ids = input_ids.to(device)
            input_mask = input_mask.to(device)
            segment_ids = segment_ids.to(device)
            label_ids = label_ids.to(device)
            claim_input_ids = claim_input_ids.to(device)
            claim_input_mask = claim_input_mask.to(device)
            claim_segment_ids = claim_segment_ids.to(device)
            claim_label_ids = claim_label_ids.to(device)

#             print("start")
#             print(input_ids)
#             print(input_mask)
#             print(segment_ids)
#             print(label_ids)
#             print(claim_input_ids)
#             print(claim_input_mask)
#             print(claim_segment_ids)
#             print(claim_label_ids)
#             print("end")
            with torch.no_grad():
                tmp_eval_loss = model(input_ids=input_ids, token_type_ids=segment_ids, attention_mask=input_mask, labels=label_ids, input_ids2=claim_input_ids, token_type_ids2=claim_segment_ids, attention_mask2=claim_input_mask, labels2=claim_label_ids)
                
                logits = model(input_ids=input_ids, token_type_ids=segment_ids, attention_mask=input_mask, input_ids2=claim_input_ids, token_type_ids2=claim_segment_ids, attention_mask2=claim_input_mask)
            
#             print(logits)
#             print(logits[0])
            logits = logits.detach().cpu().numpy()
            print(logits)
            label_ids = label_ids.to('cpu').numpy()
#             print(label_ids)

            # Micro F1 (aggregated tp, fp, fn counts across all examples)
            tmp_tp, tmp_pred_c, tmp_gold_c = tp_pcount_gcount(logits, label_ids)
            eval_tp += tmp_tp
            eval_pred_c += tmp_pred_c
            eval_gold_c += tmp_gold_c
            
            pred_label = np.argmax(logits, axis=1)
            raw_score += zip(logits, pred_label, label_ids)
            
            # Macro F1 (averaged P, R across mini batches)
            tmp_eval_p, tmp_eval_r, tmp_eval_f1 = p_r_f1(logits, label_ids)

            eval_macro_p += tmp_eval_p
            eval_macro_r += tmp_eval_r

            eval_loss += tmp_eval_loss.mean().item()
            nb_eval_examples += input_ids.size(0)
            nb_eval_steps += 1


        # Micro F1 (aggregated tp, fp, fn counts across all examples)
        eval_micro_p = eval_tp / eval_pred_c
        eval_micro_r = eval_tp / eval_gold_c
        eval_micro_f1 = 2 * eval_micro_p * eval_micro_r / (eval_micro_p + eval_micro_r)

        # Macro F1 (averaged P, R across mini batches)
        eval_macro_p = eval_macro_p / nb_eval_steps
        eval_macro_r = eval_macro_r / nb_eval_steps
        eval_macro_f1 = 2 * eval_macro_p * eval_macro_r / (eval_macro_p + eval_macro_r)

        eval_loss = eval_loss / nb_eval_steps
        result = {
                  'eval_loss': eval_loss,
                  'eval_micro_p': eval_micro_p,
                  'eval_micro_r': eval_micro_r,
                  'eval_micro_f1': eval_micro_f1,
                  'eval_macro_p': eval_macro_p,
                  'eval_macro_r': eval_macro_r,
                  'eval_macro_f1': eval_macro_f1,
#                   'global_step': global_step,
#                   'loss': tr_loss/nb_tr_steps
                  }

        output_eval_file = os.path.join(output_dir, "xibmcs_original_cos_test_eval_results.txt")
        output_raw_score = os.path.join(output_dir, "xibmcs_original_cos_raw_score.csv")
        with open(output_eval_file, "w") as writer:
            logger.info("***** Eval results *****")
            for key in sorted(result.keys()):
                logger.info("  %s = %s", key, str(result[key]))
                writer.write("%s = %s\n" % (key, str(result[key])))

        with open(output_raw_score, 'w') as fout:
            fields = ["undermine_score", "support_score","predict_label", "gold"]
            writer = csv.DictWriter(fout, fieldnames=fields)
            writer.writeheader()
            for score, pred, gold in raw_score:
                writer.writerow({
                    "undermine_score": str(score[0]),
                    "support_score": str(score[1]),
                    "predict_label": str(pred),
                    "gold": str(gold)
                })

In [ ]:
def experiments():
    data_dir = "D:/Jupyter/data/dataset/perspective_stances/"
#     data_dir = "/home/syg340/Dataset/"

    # data_dir_output = data_dir + "output2/"
    data_dir_output = "D:/Projects/Stance/Models/"
    train_and_test(data_dir=data_dir, do_train=True, do_eval=True, output_dir=data_dir_output,task_name="Mrpc")


In [14]:
def evaluation_with_pretrained():
    bert_model = "D:/Projects/Stance/Models/Consistency_Cues/consistencycues_v4.pth"
#     bert_model = "D:/Projects/Stance/Models/dataExpantion/consistencycue_expansion.pth"
    
#     data_dir = "D:/Jupyter/data/dataset/perspective_stances/"
    data_dir = "D:/Jupyter/data/dataset/ibmcs/"
#     data_dir = "D:/Projects/Stance/Dataset/BertForOppositeClassification/"
#     data_dir = "D:/Projects/Stance/Dataset/OnlyNew/"
    # data_dir_output = data_dir + "output2/"
    ## v2: concat
    ## v3: multiply
    data_dir_output = "D:/Projects/Stance/Evaluation/bert_dummy_output/ConsistencyCues_local/"
    train_and_test(data_dir=data_dir, do_train=False, do_eval=True, output_dir=data_dir_output,task_name="mrpc",saved_model=bert_model)

In [15]:
if __name__ == "__main__":
#     experiments()
    evaluation_with_pretrained()

06/23/2020 19:19:50 - INFO - run_classifier -   device cuda n_gpu 1 distributed training False
06/23/2020 19:19:55 - INFO - transformers.tokenization_utils -   loading file https://s3.amazonaws.com/models.huggingface.co/bert/bert-base-uncased-vocab.txt from cache at C:\Users\arsen\.cache\torch\transformers\26bc1ad6c0ac742e9b52263248f6d0f00068293b33709fae12320c0e35ccfbbb.542ce4285a40d23a559526243235df47c5f75c197f04f37d1a0c124c32c9a084
06/23/2020 19:19:55 - INFO - run_classifier -   *** Example ***
06/23/2020 19:19:55 - INFO - run_classifier -   guid: test-1
06/23/2020 19:19:55 - INFO - run_classifier -   tokens: [CLS] this house believes that open primaries are the most effective method of selecting candidates for [SEP] a single election in which the party nominee is selected by non ##par ##ty [SEP]
06/23/2020 19:19:55 - INFO - run_classifier -   input_ids: 101 2023 2160 7164 2008 2330 27419 2024 1996 2087 4621 4118 1997 17739 5347 2005 102 1037 2309 2602 1999 2029 1996 2283 9773 2003 3

06/23/2020 19:19:57 - INFO - run_classifier -   guid: test-5
06/23/2020 19:19:57 - INFO - run_classifier -   tokens: [CLS] this house believes that open primaries are the most effective method of selecting candidates for elections [SEP]
06/23/2020 19:19:57 - INFO - run_classifier -   input_ids: 101 2023 2160 7164 2008 2330 27419 2024 1996 2087 4621 4118 1997 17739 5347 2005 3864 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0
06/23/2020 19:19:57 - INFO - run_classifier -   input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0
06/23/2020 19:19:57 - INFO - run_classifier -   segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
06/23/2020 19:19:57 - INFO - run_classifier -   label: 1 (id = 1)
06/23/2020 19:19:58 - INFO - run_classifier -   ***** Running evaluation *****
06/23/2020 19:19:58 - INFO - run_classifier -     Num examples = 2394
06/23/2020 19:19:58 - INFO - run_classifier -     Batch size = 8
06/23/2020 19:20:01 - INFO - pytorch_pretrained_bert.mode

logits_ce:
tensor([[ 0.6127, -0.4101],
        [-0.1317,  0.4436],
        [-2.4653,  2.2480],
        [ 0.3183,  0.2886],
        [-1.9076,  1.5766],
        [-0.3535,  0.5258],
        [ 0.2335,  0.2879],
        [ 2.1746, -2.3448]], device='cuda:0')
logits_cos:
tensor([[ 0.5713, -0.5783],
        [-0.0400,  0.4816],
        [-1.9046,  2.8597],
        [ 0.1267,  0.0176],
        [-1.3378,  2.1368],
        [-0.1841,  0.6794],
        [ 0.0935,  0.0642],
        [ 1.8421, -2.8147]], device='cuda:0')
logits_ce:
tensor([[ 0.6127, -0.4101],
        [-0.1317,  0.4436],
        [-2.4653,  2.2480],
        [ 0.3183,  0.2886],
        [-1.9076,  1.5766],
        [-0.3535,  0.5258],
        [ 0.2335,  0.2879],
        [ 2.1746, -2.3448]], device='cuda:0')
logits_cos:
tensor([[ 0.5713, -0.5783],
        [-0.0400,  0.4816],
        [-1.9046,  2.8597],
        [ 0.1267,  0.0176],
        [-1.3378,  2.1368],
        [-0.1841,  0.6794],
        [ 0.0935,  0.0642],
        [ 1.8421, -2.8147]], dev

logits_cos:
tensor([[-0.2434,  0.7353],
        [-0.3989,  0.8585],
        [-0.5242,  1.0697],
        [ 0.0786,  0.1357],
        [ 0.9126, -1.6925],
        [-0.3919,  0.9459],
        [-0.0739,  0.3438],
        [ 0.1404,  0.1664]], device='cuda:0')
logits_ce:
tensor([[-0.1896,  0.8824],
        [-0.4845,  0.8443],
        [-0.6427,  0.9972],
        [ 0.2218,  0.3251],
        [ 1.2324, -1.3308],
        [-0.4760,  0.9133],
        [-0.0800,  0.3337],
        [ 0.1521,  0.2012]], device='cuda:0')
logits_cos:
tensor([[-0.2434,  0.7353],
        [-0.3989,  0.8585],
        [-0.5242,  1.0697],
        [ 0.0786,  0.1357],
        [ 0.9126, -1.6925],
        [-0.3919,  0.9459],
        [-0.0739,  0.3438],
        [ 0.1404,  0.1664]], device='cuda:0')
[[-0.2433805   0.7352859 ]
 [-0.3988969   0.85846335]
 [-0.52417874  1.0696591 ]
 [ 0.07860906  0.13572565]
 [ 0.9125928  -1.6924684 ]
 [-0.3918909   0.9458587 ]
 [-0.07394964  0.3437897 ]
 [ 0.14037032  0.16643146]]
logits_ce:
tensor([[ 1

tensor([[ 0.7311, -0.0729],
        [ 0.8975, -0.2693],
        [-0.6803,  1.0843],
        [ 1.1757, -0.5268],
        [-0.4909,  1.0620],
        [ 0.3482,  0.2917],
        [-0.3499,  0.9715],
        [ 0.8308, -0.1665]], device='cuda:0')
logits_cos:
tensor([[ 0.3874, -0.4755],
        [ 0.4813, -0.7051],
        [-0.5870,  1.1393],
        [ 0.7673, -1.0415],
        [-0.5007,  1.0025],
        [ 0.1226, -0.0060],
        [-0.3710,  0.8598],
        [ 0.4600, -0.5878]], device='cuda:0')
logits_ce:
tensor([[ 0.7311, -0.0729],
        [ 0.8975, -0.2693],
        [-0.6803,  1.0843],
        [ 1.1757, -0.5268],
        [-0.4909,  1.0620],
        [ 0.3482,  0.2917],
        [-0.3499,  0.9715],
        [ 0.8308, -0.1665]], device='cuda:0')
logits_cos:
tensor([[ 0.3874, -0.4755],
        [ 0.4813, -0.7051],
        [-0.5870,  1.1393],
        [ 0.7673, -1.0415],
        [-0.5007,  1.0025],
        [ 0.1226, -0.0060],
        [-0.3710,  0.8598],
        [ 0.4600, -0.5878]], device='cuda:0

...

logits_ce:
tensor([[ 1.4338, -1.4888],
        [ 0.8607, -0.6933],
        [ 0.5252, -0.4669],
        [ 0.3338, -0.0703],
        [ 0.6968, -0.4320],
        [-1.1368,  1.2911],
        [ 1.2920, -1.4352],
        [ 1.5809, -1.8162]], device='cuda:0')
logits_cos:
tensor([[ 1.0299, -1.6408],
        [ 0.6393, -0.7764],
        [ 0.4058, -0.5655],
        [ 0.2446, -0.0099],
        [ 0.5080, -0.6074],
        [-0.7787,  1.7000],
        [ 0.9829, -1.7506],
        [ 1.2156, -2.1615]], device='cuda:0')
[[ 1.0298797  -1.6408058 ]
 [ 0.63933134 -0.7764159 ]
 [ 0.4058304  -0.56551474]
 [ 0.2445809  -0.00991058]
 [ 0.50796664 -0.60736144]
 [-0.77873796  1.7000301 ]
 [ 0.9829441  -1.7505957 ]
 [ 1.2155713  -2.1615336 ]]
logits_ce:
tensor([[ 1.3597, -1.4921],
        [ 1.7978, -1.9626],
        [ 0.7310, -0.7190],
        [-1.0290,  1.0541],
        [-1.5500,  1.4492],
        [ 1.0291, -1.0309],
        [ 0.6224, -0.5543],
        [-0.8068,  1.0208]], device='cuda:0')
logits_cos:
tensor([[ 0

logits_ce:
tensor([[ 0.5141, -0.4043],
        [-0.4376,  0.8131],
        [ 0.5501, -0.5092],
        [-1.0668,  1.2665],
        [ 2.1159, -2.2577],
        [ 2.1462, -2.2844],
        [-1.3325,  1.3589],
        [-0.3091,  0.7002]], device='cuda:0')
logits_cos:
tensor([[ 0.4354, -0.4892],
        [-0.3021,  0.9670],
        [ 0.4115, -0.5422],
        [-0.7009,  1.6268],
        [ 1.7251, -2.7036],
        [ 1.7455, -2.7582],
        [-0.9189,  1.6981],
        [-0.2477,  0.8111]], device='cuda:0')
[[ 0.43539098 -0.48922756]
 [-0.30210835  0.9669504 ]
 [ 0.4114717  -0.54215807]
 [-0.7009471   1.6267533 ]
 [ 1.7250519  -2.7035935 ]
 [ 1.7454836  -2.7581613 ]
 [-0.91894406  1.6981462 ]
 [-0.24765354  0.8111056 ]]
logits_ce:
tensor([[-0.0501,  0.4328],
        [ 0.8460, -0.7396],
        [ 0.3298, -0.0852],
        [-0.8275,  1.0762],
        [ 2.3037, -2.4411],
        [-0.5387,  0.8863],
        [ 0.0466,  0.1865],
        [ 2.4024, -2.4478]], device='cuda:0')
logits_cos:
tensor([[-0

logits_ce:
tensor([[-0.1776,  0.4386],
        [ 0.8095, -0.7731],
        [ 0.1193,  0.1000],
        [-0.4492,  0.7557],
        [ 0.3756, -0.2019],
        [ 1.0562, -1.0730],
        [ 0.0809,  0.1536],
        [ 0.1424,  0.0724]], device='cuda:0')
logits_cos:
tensor([[-0.1972,  0.4388],
        [ 0.5539, -0.9856],
        [ 0.0445,  0.0248],
        [-0.3545,  0.7964],
        [ 0.2425, -0.3255],
        [ 0.7835, -1.3579],
        [-0.0287,  0.1037],
        [ 0.0347,  0.0331]], device='cuda:0')
[[-0.19724634  0.4387609 ]
 [ 0.553938   -0.98556894]
 [ 0.04447085  0.02477757]
 [-0.35446313  0.79638356]
 [ 0.24253576 -0.32548794]
 [ 0.78346837 -1.3578923 ]
 [-0.02866667  0.10372028]
 [ 0.03474117  0.03305689]]
logits_ce:
tensor([[ 0.0318,  0.1818],
        [ 0.8083, -0.7661],
        [-0.2522,  0.6314],
        [-1.0933,  1.6288],
        [ 1.4324, -1.4956],
        [ 0.8641, -0.8345],
        [-0.3573,  1.0909],
        [-0.3687,  0.7898]], device='cuda:0')
logits_cos:
tensor([[-0

06/23/2020 19:21:09 - INFO - run_classifier -   ***** Eval results *****
06/23/2020 19:21:09 - INFO - run_classifier -     eval_loss = 1.5085398965577284
06/23/2020 19:21:09 - INFO - run_classifier -     eval_macro_f1 = 0.6999447886963139
06/23/2020 19:21:09 - INFO - run_classifier -     eval_macro_p = 0.6662460317460323
06/23/2020 19:21:09 - INFO - run_classifier -     eval_macro_r = 0.7372341269841275
06/23/2020 19:21:09 - INFO - run_classifier -     eval_micro_f1 = 0.6971136280599196
06/23/2020 19:21:09 - INFO - run_classifier -     eval_micro_p = 0.6756373937677054
06/23/2020 19:21:09 - INFO - run_classifier -     eval_micro_r = 0.72


logits_ce:
tensor([[-0.3213,  0.5791],
        [ 0.4366, -0.3362]], device='cuda:0')
logits_cos:
tensor([[-0.2178,  0.6361],
        [ 0.2382, -0.4529]], device='cuda:0')
[[-0.21781528  0.636083  ]
 [ 0.23818187 -0.45290726]]
